In [1]:
import numpy as np
import utils
import pandas as pd

In [2]:
synth_regular = utils.load_synthetic()
compas = utils.load_compas_alt()
RESPONSE = "score_factor"

In [3]:
compas.keys()

dict_keys(['train', 'test'])

In [4]:
#compas["standard"]["train"].keys()

In [5]:
#Checking that the classes don't become too much more imbalanced when data is removed.

#Synthetic data
for key, value in synth_regular.items():
    #print(value.columns)
    print("Key: ", key)
    print("Caucasian = 1: ",len(value[value["is_Caucasian"]==1])/len(value) ,
    "\nCaucasian = 0: ", len(value[value["is_Caucasian"]==0])/len(value))
    print("Male = 1: ",len(value[value["gender_factor"]==1])/len(value) ,
    "\nMale = 0: ", len(value[value["gender_factor"]==0])/len(value))
    print("After 30% missing: ")
    temp = value.copy()
    temp = utils.impute(utils.data_remover_cat(temp, "is_Caucasian", 30), "is_Caucasian")
    print("Caucasian = 1: ",len(temp[temp["is_Caucasian"]==1])/len(temp) ,
        "\nCaucasian = 0: ", len(temp[temp["is_Caucasian"]==0])/len(temp))
    print("Male = 1: ",len(temp[temp["gender_factor"]==1])/len(temp) ,
        "\nMale = 0: ", len(temp[temp["gender_factor"]==0])/len(temp))

Key:  test
Caucasian = 1:  0.34634634634634637 
Caucasian = 0:  0.6536536536536537
Male = 1:  0.8198198198198198 
Male = 0:  0.18018018018018017
After 30% missing: 
Caucasian = 1:  0.32363907531692765 
Caucasian = 0:  0.6763609246830723
Male = 1:  0.8553318419090231 
Male = 0:  0.14466815809097688
Key:  train
Caucasian = 1:  0.33683158420789605 
Caucasian = 0:  0.663168415792104
Male = 1:  0.8140929535232384 
Male = 0:  0.18590704647676162
After 30% missing: 
Caucasian = 1:  0.27421758569299554 
Caucasian = 0:  0.7257824143070045
Male = 1:  0.8524590163934426 
Male = 0:  0.14754098360655737


In [6]:
a = []
b = [1,2,3]
c = [4,5,56]
a.append(b)
a.append(c)
np.mean(a, axis = 0)

array([ 2.5,  3.5, 29.5])

In [7]:
#Compas data
"""for ver in ["standard", "violent"]:
    print("Compas dataset type: ", ver)"""
for key, value in compas.items():
    #print(value.columns)
    print("Key: ", key)
    print("Caucasian = 1: ",len(value[value["is_Caucasian"]==1])/len(value) ,
    "\nCaucasian = 0: ", len(value[value["is_Caucasian"]==0])/len(value))
    print("Male = 1: ",len(value[value["gender_factor"]==1])/len(value) ,
    "\nMale = 0: ", len(value[value["gender_factor"]==0])/len(value))
    print("Score text: ", len(value[value["score_factor"]==1])/len(value))
    print("After 30% missing: ")
    temp = value.copy()
    temp = utils.impute(utils.data_remover_cat(temp, "is_Caucasian", 30), "is_Caucasian")
    print("Caucasian = 1: ",len(temp[temp["is_Caucasian"]==1])/len(temp) ,
        "\nCaucasian = 0: ", len(temp[temp["is_Caucasian"]==0])/len(temp))
    print("Male = 1: ",len(temp[temp["gender_factor"]==1])/len(temp) ,
        "\nMale = 0: ", len(temp[temp["gender_factor"]==0])/len(temp))
    print("Score text: ", len(value[value["score_factor"]==1])/len(value))


Key:  train
Caucasian = 1:  0.3388149939540508 
Caucasian = 0:  0.6611850060459492
Male = 1:  0.8099153567110037 
Male = 0:  0.19008464328899638
Score text:  0.44401451027811367
After 30% missing: 
Caucasian = 1:  0.32952924393723254 
Caucasian = 0:  0.6704707560627675
Male = 1:  0.8088445078459344 
Male = 0:  0.19115549215406563
Score text:  0.44401451027811367
Key:  test
Caucasian = 1:  0.3446244477172312 
Caucasian = 0:  0.6553755522827688
Male = 1:  0.8090328915071183 
Male = 0:  0.19096710849288168
Score text:  0.4491899852724595
After 30% missing: 
Caucasian = 1:  0.3361462728551336 
Caucasian = 0:  0.6638537271448663
Male = 1:  0.7883263009845288 
Male = 0:  0.21167369901547117
Score text:  0.4491899852724595


In [8]:
a = pd.DataFrame({"a":[1,2,3], "b":[3,4,5]})
b = pd.DataFrame({"a":[1,2,3], "b":[3,4,5]})
a==b

a     b
0  True  True
1  True  True
2  True  True

In [9]:
percentiles = [p for p in range(0,20,2)]+[p for p in range(20,60, 10)]
missing=["priors_count", "two_year_recid", "is_Caucasian", "gender_factor", "crime_factor"]
all_results = {}
RUNS = 30
for miss in missing:
    for sensitive in ["is_Caucasian", "gender_factor"]:
        try:
            recid_results = utils.test_bench(data = "compas", pred = RESPONSE, missing = miss, sensitive=sensitive,
                            percentiles = percentiles, n_runs=RUNS)
            synth_results = utils.test_bench(data = "synthetic", pred = RESPONSE, missing = miss, sensitive=sensitive,
                                percentiles = percentiles, n_runs=RUNS)
            #TODO and remember to fix data v_recid_results = utils.test_bench(train = compas["standard"]["train"],test = compas["standard"]["test"], pred = RESPONSE, missing = miss, sensitive=sensitive,
                            #percentiles = percentiles)
            all_results[miss+"_"+sensitive+"_"+"synth"] = synth_results 
            all_results[miss+"_"+sensitive+"_"+"recid"] = recid_results 
        except:
            print("failed at " + sensitive + missing)
        """try:
            synth_results = utils.test_bench(train = synth_regular["train"],test = synth_regular["test"], pred = RESPONSE, missing = miss, sensitive=sensitive,
                            percentiles = percentiles)
            recid_results = utils.test_bench(train = compas["train"],test = compas["test"], pred = RESPONSE, missing = miss, sensitive=sensitive,
                            percentiles = percentiles)
            #TODO and remember to fix data v_recid_results = utils.test_bench(train = compas["standard"]["train"],test = compas["standard"]["test"], pred = RESPONSE, missing = miss, sensitive=sensitive,
                            #percentiles = percentiles)
            all_results[miss+"_"+sensitive+"_"+"synth"] = synth_results 
            all_results[miss+"_"+sensitive+"_"+"recid"] = recid_results 
            #all_results[miss+"_"+sensitive+"_"+"v_recid"] = v_recid_results
        except Exception as e:
            print("Exception: ", e)
            print("Parameters: ", sensitive+"_"+miss) 
        """

 10%|█         | 3/30 [03:10<28:39, 63.67s/it]

PP error z0
PP error z0
PP error z0


 20%|██        | 6/30 [06:17<25:05, 62.73s/it]

PP error z0
PP error z0
PP error z0


  0%|          | 0/30 [01:15<?, ?it/s]


TypeError: can only concatenate str (not "list") to str

In [12]:
all_results['gender_factor_gender_factor_recid']

{'0': {'mar': {'acc': {'log_reg': {'cca': [0.7486499754540992,
      0.7461953853706431,
      0.7461953853706431,
      0.7461953853706431,
      0.750613647520864,
      0.7511045655375552,
      0.7476681394207167,
      0.7452135493372607,
      0.7442317133038783,
      0.7466863033873343,
      0.7447226313205695,
      0.7407952871870398,
      0.7344133529700541,
      0.7295041728031418],
     'mean': [0.7486499754540992,
      0.7486499754540992,
      0.7486499754540992,
      0.7486499754540992,
      0.7476681394207167,
      0.7471772214040255,
      0.7466863033873343,
      0.7486499754540992,
      0.7486499754540992,
      0.7476681394207167,
      0.7466863033873343,
      0.7486499754540992,
      0.748159057437408,
      0.7427589592538046],
     'mice_def': [0.7486499754540992,
      0.7486499754540992,
      0.7486499754540992,
      0.7486499754540992,
      0.7486499754540992,
      0.7486499754540992,
      0.7486499754540992,
      0.748159057437408,
      0.

In [10]:
all_results['priors_count_is_Caucasian_synth']["0"]["mar"]["acc"]["log_reg"]

{'cca': [1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  0.8043043043043043,
  0.7167167167167167,
  0.7297297297297297],
 'mean': [1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0],
 'mice_def': [1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0,
  1.0]}

In [ ]:
all_results['priors_count_is_Caucasian_synth']["0"]["mar"]["pp"]["log_reg"]

{'cca': [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
 'mean': [0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0],
 'mice_def': [0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0]}

In [ ]:
all_results['priors_count_is_Caucasian_synth']["0"]["mar"]["spd"]["log_reg"]

{'cca': [0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218],
 'mean': [0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218],
 'mice_def': [0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218,
  0.4218697512420218]}

In [13]:
import json
from pathlib import Path
with open(Path("raw_data/multi_23_06.json"), 'w') as f:
            json.dump(all_results, f)